# Introduction to mathematical statistics 

Welcome to the lecture 10 in 02403

During the lectures we will present both slides and notebooks. 


In [ ]:
import numpy as np
import matplotlib.pyplot as plt
import pandas as pd
import scipy.stats as stats
import statsmodels.api as sm
import statsmodels.formula.api as smf
import statsmodels.stats.power as smp
import statsmodels.stats.proportion as smprop

### Example: Intro to ANOVA

Is there a difference (in mean) between groups A, B, and C?
Analysis of variance (ANOVA) can be used for the analysis, <br>
provided **the observations in each group can be assumed to be normally distributed.**

| Group A | Group B | Group C |
|---------|---------|---------|
| 2.8     | 5.5     | 5.8     |
| 3.6     | 6.3     | 8.3     |
| 3.4     | 6.1     | 6.9     |
| 2.3     | 5.7     | 6.1     |


In [ ]:
# Make pandas dataframe with grouped data:
data = pd.DataFrame({
    'value':  [2.8, 3.6, 3.4, 2.3, 5.5, 6.3, 6.1, 5.7, 5.8, 8.3, 6.9, 6.1], 
    'group':  ["A", "A", "A", "A", "B", "B", "B", "B", "C", "C", "C", "C"]})
data

In [ ]:
data.plot.scatter('group', 'value') # Pandas scatter plot

In [ ]:
data.boxplot(by="group", showmeans=True) # Pandas boxplot

The three groups have different means - indicated by the green triangles

### Example: Estimate parameters $\mu$, $\alpha_i$ and $\sigma^2$

In [ ]:
# Compute the overall mean and add to dataframe:
data['overall_mean'] = data["value"].mean()
data

In [ ]:
# compute the mean within each group and add to dataframe:
data['group_mean'] = data.groupby("group")['value'].transform('mean')
data

In [ ]:
# compute the "alpha" for each group and add to dataframe:
data["alpha"] = data["group_mean"] - data["overall_mean"]
data

### Variation within groups (Residual variation left after the model):

$
SSE = \sum_{i=1}^{k} \sum_{j=1}^{n_i} \left( y_{ij} - \bar{y}_i \right)^2
$

In [ ]:
# calculate the individual contribution to SSE and add to dataframe:
data['sse_contribution'] = (data['value']-data['group_mean'])**2
data



$
\hat{\sigma}^2 = MSE = \frac{SSE}{n-k}
$

In [ ]:
# calculate SSE and MSE:
SSE = data["sse_contribution"].sum()
MSE = SSE / (12-3)
print([SSE, MSE])

LM Method

In [ ]:
one = np.repeat(1,4)
zero = np.repeat(0,4)
col1 = np.append(np.append(one,zero),zero)
col2 = np.append(np.append(zero,one),zero)
col3 = np.append(np.append(zero,zero),one)

X1 =np.array([col1,col2,col3]).T

col1 = np.append(np.append(one,one),one)
X2 =np.array([col1,col2,col3]).T

col2 = np.append(np.append(one,zero),-one)
col3 = np.append(np.append(zero,one),-one)


X3 =np.array([col1,col2,col3]).T
X3

Try to calculate H for all design matrices to check that results are the same

In [ ]:
H = X1@np.linalg.inv(X1.T@X1)@X1.T
X0 = np.array([np.repeat(1,12)]).T
H0 = (1/(X0.T@X0))*(X0@X0.T)
I = np.identity(12)
y = data["value"]
SST = y.T @ (I-H0) @ y
SSE = y.T @ (I-H) @ y
SSTr = y.T @ (H-H0) @ y

dfSSE = np.sum(np.diag(I-H))
dfTr = np.sum(np.diag(H-H0))
dfTot = np.sum(np.diag(I-H0))
## Coefficient table
aov_Tab = np.array([[dfTr,dfSSE,dfTot],[SSTr,SSE,SST],
                    [SSTr/dfTr,SSE/dfSSE,SST/dfTot]]).T
col_names = ["df","SS","ME"]
row_names = ["Treatment","Residual","Total"]
aov_Tab = pd.DataFrame(aov_Tab,columns = col_names, index = row_names)
aov_Tab

### Example: ANOVA table with python

In [ ]:
# Make the ANOVA table:
fit = smf.ols("value ~ group", data=data).fit()
anova_table = sm.stats.anova_lm(fit)
print(anova_table)


In [ ]:
print(fit.summary(fit,slim=True))

In [ ]:
np.linalg.inv(X2.T@X2)@X2.T@y

In [ ]:
data.boxplot(column="value", by="group", showmeans=True) # Pandas boxplot

As in chapter 8

In [ ]:
np.linalg.inv(X3.T@X3)@X3.T@y

In [ ]:
# compare with values in ANOVA table:
print(anova_table)

## Skive Fjord

Is the an effect of "vandmiljø"-plans? Use the September. 

In [ ]:
SkiveAvg = pd.read_csv("../week1/skiveAvg.csv", sep=';')
SkiveAvg["vmp"] = pd.Categorical(SkiveAvg["vmp"])
SkiveAvg

In [ ]:
dat_september = SkiveAvg[SkiveAvg["month"]==9] ## Only September
fit = smf.ols("Nload ~ vmp", data=dat_september).fit()
anova_table = sm.stats.anova_lm(fit)
print(anova_table)

Residual analysis

In [ ]:
dat_september.boxplot("Nload",by="vmp")

In [ ]:
vmp = SkiveAvg["vmp"]
vmp = vmp[SkiveAvg["month"]==9]

rstudent = fit.outlier_test()
rstudent["vmp"] = vmp
rstudent.boxplot("student_resid",by="vmp")


In [ ]:
e = rstudent["student_resid"]
n = len(e)
e1 = e[1:(n-1)]
e2 = np.roll(e,-1)[1:(n-1)]
print(np.corrcoef(e1,e2)[0,1])
rstudent["student_resid"]

In [ ]:
n = len(rstudent["student_resid"])
fig = sm.qqplot(rstudent["student_resid"], stats.t, distargs=(n-4,),loc=0,scale=1,line="q",a=1/2)
plt.show()

## Post hoc comparison

In [ ]:
M = 4 * 3 / 2
alpha_bon = 0.05 / M
n0 = np.sum(vmp==0)
n1 = np.sum(vmp==1)
n2 = np.sum(vmp==2)
n3 = np.sum(vmp==3)
dat0 = dat_september[vmp==0]
dat1 = dat_september[vmp==1]
dat2 = dat_september[vmp==2]
dat3 = dat_september[vmp==3]
N_load0 = np.mean(dat0["Nload"])
N_load1 = np.mean(dat1["Nload"])
N_load2 = np.mean(dat2["Nload"])
N_load3 = np.mean(dat3["Nload"])
crit_vals = np.array([-1,1]) * stats.t.ppf(1-alpha_bon,df=n-4) 
sig = np.sqrt(fit.scale)

CI01 = N_load0 - N_load1 + crit_vals * sig * np.sqrt(1/n0+1/n1)
CI02 = N_load0 - N_load2 + crit_vals * sig * np.sqrt(1/n0+1/n2)
CI03 = N_load0 - N_load3 + crit_vals * sig * np.sqrt(1/n0+1/n3)
CI12 = N_load1 - N_load2 + crit_vals * sig * np.sqrt(1/n1+1/n2)
CI13 = N_load1 - N_load3 + crit_vals * sig * np.sqrt(1/n1+1/n3)
CI23 = N_load2 - N_load3 + crit_vals * sig * np.sqrt(1/n2+1/n3)

np.array([[CI01],[CI02],[CI03],[CI12],[CI13],[CI23]])

In [ ]:
np.array([n0,n1,n2,n3])